In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline

In [ ]:
!ls

In [ ]:
# Εισάγουμε τις βοηθητικές συναρτήσεις απο το auxiliary.py
from auxiliary import *

In [ ]:
# model function
def y(x): return 0.3*sin(x) + sin(1.3*x) + 0.9*sin(4.2*x)

# plot model function
xcurve = linspace(-2, 4, 101)
plt.plot(xcurve, y(xcurve), label='y(x)')
Gll('x', 'y')
plt.grid(True)

In [ ]:
# initialise random numbers generator
#seed(1234) # use a fixed seed, so every time we run this code
           # we will get the same results

# population
ninds = 24               # number of individuals: population size
xmin, xmax = -2.0, 4.0# limits
X = Random(ninds, xmin, xmax) # generate numbers between 0 and 4*pi

# just for the sake of showing nice numbers in this notebook:
#X = array(X, dtype=int)    # truncate values
#X = array(X, dtype=float)  # revert to float
print('Population:\n', X)

In [ ]:
plt.plot(xcurve, y(xcurve), label='y(x)')
plt.plot(X, y(X), 'ro', label='population')
Gll('x', 'y', 'upper left')
plt.grid(True)

In [ ]:
ngenes = 20
# compute chromosome from x
def cFcn(x): return SimpleChromo(x, ngenes)

# compute x from chromosome
def xFcn(c): return sum(c)

In [ ]:
C = array([cFcn(x) for x in X])
print(C)

In [ ]:
def objFcn(c):
    x = xFcn(c)
    if x < xmin or x > xmax: return -100.0*(1.0+abs(x))
    return y(x)

In [ ]:
Y = array([objFcn(c) for c in C]) # objective values
PrintPop(C, Y, xFcn, showC=True)

In [ ]:
# Ορισμός της καινούριας fitness function
def Fitness2(Y):
    ymin, ymax = min(Y), max(Y)
    if abs(ymax - ymin) < 1e-14: return ones(len(Y))
    return (Y - ymin) / (ymax - ymin)

In [ ]:
# compute fitness from objective values
F = Fitness2(Y)                

# sort in decreasing order of fitness
C, Y, F = SortPop(C, Y, F)
PrintPop(C, Y, xFcn, F)

In [ ]:
# probabilities
P = F / sum(F)

# cumulated probabilities
M = cumsum(P)
PrintPop(C, Y, xFcn, F, P, M)

In [ ]:
def Evolve(C, xFcn, objFcn, ngen=10, elite=True, pc=0.8, pm=0.01, verb=False, showC=False):

    # objective values
    Y = array([objFcn(c) for c in C]) # objective values
    ninds = len(C)
    nbases = len(C[0])

    # fitness and probabilities (sorted)
    F = Fitness2(Y)
    C, Y, F = SortPop(C, Y, F)
    P = F / sum(F)
    M = cumsum(P)

    # results
    OV = zeros(ngen+1)
    OV[0] = Y[0] # best first objective value

    # evolution
    for gen in range(ngen):

        # best individual
        bestC = C[0].copy()
        bestY = Y[0]

        # print generation
        if gen==0 or verb:
            print
            PrintPop(C, Y, xFcn, F, showC=showC)

        # selection
        S = RouletteSelect(M, ninds)
        idxA, idxB = FilterPairs(S)
        
        # reproduction
        Cnew = [] # new chromosomes
        for k in range(ninds//2):

            # parents
            A, B = C[idxA[k]], C[idxB[k]]

            # crossover
            if FlipCoin(pc):
                pos = randint(1, nbases-1)
                a = hstack([A[:pos], B[pos:]])
                b = hstack([B[:pos], A[pos:]])
            else:
                a, b = A.copy(), B.copy()

            # mutation
            if FlipCoin(pm):
                pos  = randint(0, nbases)
                bmax = max(a)
                if FlipCoin(0.5): a[pos] += bmax * 1.1
                else:             a[pos] -= bmax * 1.1

            # new individuals
            Cnew.append(a)
            Cnew.append(b)

        # new population
        C = array(Cnew)
        Y = array([objFcn(c) for c in C]) # objective values
        F = Fitness2(Y)

        # elitism
        if elite:
            I = F.argsort()[::-1] # the [::-1] is a trick to reverse the sorting order
            best  = I[0]
            worst = I[len(I)-1]
            if bestY >  Y[worst]:
                C[worst] = bestC
                Y[worst] = bestY
                F = Fitness2(Y)

        # probabilities (sorted)
        C, Y, F = SortPop(C, Y, F)
        P = F / sum(F)
        M = cumsum(P)

        # objective values
        OV[gen+1] = Y[0] # best current objective value

    # results
    return C, Y, OV

In [ ]:
# input data
ngen   = 10   # number of generations
pc     = 0.8   # probability of crossover
pm     = 0.01  # probability of mutation
elite  = 1     # use elitism
verb   = False # verbose

# run GA
C, Y, OV = Evolve(C, xFcn, objFcn, ngen, elite, verb=verb, showC=False)
X = [xFcn(c) for c in C]

# print and plot
plt.subplot(2, 1, 1)
plt.plot(xcurve, y(xcurve), label='y(x)')
print('\nFinal population:')
PrintPop(C, Y, xFcn)
sol = '\nSolution: x=%g y=%g' % (X[0], Y[0])
print(sol)

# plot results
plt.subplot(2, 1, 1)
plt.plot(X, Y, 'k*', label='final population')
Gll('x', 'y', 'upper left')
plt.grid(True)

# plot convergence graph
plt.subplot(2, 1, 2)
G = range(ngen+1)
plt.plot(G, OV, 'b.-', label=sol)
Gll('generation', 'y(x)')
plt.grid(True)
plt.show()